In [1]:
import os
import pickle
import pandas as pd
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import glob 
import numpy as np
import matplotlib.pyplot as plt
import requests
import xarray as xr
from datetime import datetime, timedelta
import h5py
import datetime
import traceback
from urllib.parse import urljoin
from concurrent.futures import ThreadPoolExecutor, as_completed
import pytz
import time
pd.set_option('display.max_rows', 500)

APE definition

morning (0600-1300 LST), afternoon (1400-2000 LST), and evening (2100-2400 LST) precipitation events in our analysis. Afternoon precipitation events (APEs) are identified as daily samples that meet the following two criteria: 1) daily precipitation peaks during the afternoon hours defined above; and 2) the afternoon precipitation is at least twice as large as the morning precipitation, and also greater than the evening precipitation (filter out organized precipitation).

In [9]:
#reading in HDF5 files

base_folder_path = '/data/rong3/annie/gpm'

start_year = 2001

end_year = 2019

# Collect all files from the specified years
all_gpm_files = []

for year in range(start_year, end_year + 1):
    
    folder_path = os.path.join(base_folder_path, str(year))
    
    gpm_files = sorted(glob.glob(os.path.join(folder_path, '*.HDF5')))
    
    all_gpm_files.extend(gpm_files)

    
# all_gpm_files = all_gpm_files[0:1000]    

# Number of files collected
print(f"Total files collected: {len(all_gpm_files)}")

Total files collected: 139536


In [13]:
#parallel processed

example_case = []

lon_lat_indices = []

base_date = datetime.datetime(1980, 1, 6, 0, 0, 0)

lat_start = 30.05

lat_end = 39.05

lon_start = -105.05

lon_end = -95.05

def convert_to_cst(seconds_since_base):
    
    if isinstance(seconds_since_base, (np.int32, np.int64)):
        
        seconds_since_base = int(seconds_since_base)
    
    time_delta = timedelta(seconds=seconds_since_base)
    
    # Calculate UTC time
    utc_time = base_date + time_delta
    
    # Convert UTC time to CST (subtract 6 hours for CST)
    cst_time = utc_time - timedelta(hours=6)
    
    # Remove timezone information to make it naive
    naive_cst_time = cst_time.replace(tzinfo=None)

    return naive_cst_time

def process_file(file):
    
    try: 
        
        if os.path.isfile(file) and os.path.getsize(file) > 0:

            with h5py.File(file, 'r', locking=False) as f:

                # Geographical filtering

                lon = f['Grid/lon'][:]

                lat = f['Grid/lat'][:]

                lon_mask = (lon >= lon_start) & (lon <= lon_end)

                lat_mask = (lat >= lat_start) & (lat <= lat_end)

                lon_indices = np.where(lon_mask)[0]

                lat_indices = np.where(lat_mask)[0]

                # Time conversion
                time = f['Grid/time'][:][0]

                lst = convert_to_cst(time)
                print(lst)

                # Precipitation filtering by geography
                precip = xr.DataArray(f['Grid/precipitation'][:][0], dims=['lon', 'lat'])

                psgp = precip.isel(lon=lon_indices, lat=lat_indices)

                # if 20% of grid points are nans, won't take domain average (psgp.shape[0] = lons, psgp.shape[1]= lats)
                #instead will return nan

                threshold_nans = (psgp.shape[0]*psgp.shape[1])*0.20

                psgp = psgp.where(psgp >= 0, np.nan)  # Replace all negative values with NaNs
                
#                 if lst.date == datetime(2001, 5, 6):
                    
#                     example_case.append((lst, psgp))

                nans = np.sum(np.isnan(psgp)).item()

                if nans < threshold_nans:

                    # domain average of precipitation 
                    domain_mean = np.nanmean(psgp)
                    
                    domain_max = np.nanmax(psgp)


                else:

                    print("too many nans")
                    # if nans are greater than 20% over the domain
                    domain_mean = np.nan
                    
                    domain_max = np.nan 


                return lst, domain_mean, domain_max

        else:

            print(f"Not a file: {file}")

            return None, None, None
        
    except (KeyError, OSError, IOError) as e:
        # Catch specific file-related exceptions
        
        print(f"Error while processing {file}: {e}")
        
        traceback.print_exc()  # Optional: print detailed stack trace
        
        return None, None, None

    except Exception as e:
        # Catch all other exceptions
        
        print(f"Unexpected error while processing {file}: {e}")
        
        traceback.print_exc()  # Optional: print detailed stack trace
        
        return None, None, None

def read_and_filter_data_sequential(files):
    
    lst_array = []
    
    precip_means = []
    
    precip_maxes = []  

    for file in files:
        
        lst, domain_mean, domain_max = process_file(file)
        
        if lst is not None:
            
            lst_array.append(lst)
            
            precip_means.append(domain_mean)
            
            precip_maxes.append(domain_max)  # Append max values

    # Convert lists to numpy arrays
    lst_array = np.array(lst_array, dtype='datetime64[ns]')
    
    precip_means = np.array(precip_means, dtype=float)
    
    precip_maxes = np.array(precip_maxes, dtype=float)

    return lst_array, precip_means, precip_maxes

lst_array, precip_means, precip_maxes = read_and_filter_data_sequential(all_gpm_files)

df = pd.DataFrame({
    'LST': lst_array,
    'mean_mmph': precip_means,
    'max_mmph': precip_maxes
}).sort_values(by='LST')

df = df.reset_index(drop=True)

print(df.shape)

2001-04-30 18:00:00
2001-04-30 18:30:00
2001-04-30 19:00:00
2001-04-30 19:30:00
2001-04-30 20:00:00
2001-04-30 20:30:00
2001-04-30 21:00:00
2001-04-30 21:30:00
2001-04-30 22:00:00
2001-04-30 22:30:00
2001-04-30 23:00:00
2001-04-30 23:30:00
2001-05-01 00:00:00
2001-05-01 00:30:00
2001-05-01 01:00:00
2001-05-01 01:30:00
2001-05-01 02:00:00
2001-05-01 02:30:00
2001-05-01 03:00:00
2001-05-01 03:30:00
2001-05-01 04:00:00
2001-05-01 04:30:00
2001-05-01 05:00:00
2001-05-01 05:30:00
2001-05-01 06:00:00
2001-05-01 06:30:00
2001-05-01 07:00:00
2001-05-01 07:30:00
2001-05-01 08:00:00
2001-05-01 08:30:00
2001-05-01 09:00:00
2001-05-01 09:30:00
2001-05-01 10:00:00
2001-05-01 10:30:00
2001-05-01 11:00:00
2001-05-01 11:30:00
2001-05-01 12:00:00
2001-05-01 12:30:00
2001-05-01 13:00:00
2001-05-01 13:30:00
2001-05-01 14:00:00
2001-05-01 14:30:00
2001-05-01 15:00:00
2001-05-01 15:30:00
2001-05-01 16:00:00
2001-05-01 16:30:00
2001-05-01 17:00:00
2001-05-01 17:30:00
2001-05-01 18:00:00
2001-05-01 18:30:00


2001-05-09 07:30:00
2001-05-09 08:00:00
2001-05-09 08:30:00
2001-05-09 09:00:00
2001-05-09 09:30:00
2001-05-09 10:00:00
2001-05-09 10:30:00
2001-05-09 11:00:00
2001-05-09 11:30:00
2001-05-09 12:00:00
2001-05-09 12:30:00
2001-05-09 13:00:00
2001-05-09 13:30:00
2001-05-09 14:00:00
2001-05-09 14:30:00
2001-05-09 15:00:00
2001-05-09 15:30:00
2001-05-09 16:00:00
2001-05-09 16:30:00
2001-05-09 17:00:00
2001-05-09 17:30:00
2001-05-09 18:00:00
2001-05-09 18:30:00
2001-05-09 19:00:00
2001-05-09 19:30:00
2001-05-09 20:00:00
2001-05-09 20:30:00
2001-05-09 21:00:00
2001-05-09 21:30:00
2001-05-09 22:00:00
2001-05-09 22:30:00
2001-05-09 23:00:00
2001-05-09 23:30:00
2001-05-10 00:00:00
2001-05-10 00:30:00
2001-05-10 01:00:00
2001-05-10 01:30:00
2001-05-10 02:00:00
2001-05-10 02:30:00
2001-05-10 03:00:00
2001-05-10 03:30:00
2001-05-10 04:00:00
2001-05-10 04:30:00
2001-05-10 05:00:00
2001-05-10 05:30:00
2001-05-10 06:00:00
2001-05-10 06:30:00
2001-05-10 07:00:00
2001-05-10 07:30:00
2001-05-10 08:00:00


2001-05-17 21:00:00
2001-05-17 21:30:00
2001-05-17 22:00:00
2001-05-17 22:30:00
2001-05-17 23:00:00
2001-05-17 23:30:00
2001-05-18 00:00:00
2001-05-18 00:30:00
2001-05-18 01:00:00
2001-05-18 01:30:00
2001-05-18 02:00:00
2001-05-18 02:30:00
2001-05-18 03:00:00
2001-05-18 03:30:00
2001-05-18 04:00:00
2001-05-18 04:30:00
2001-05-18 05:00:00
2001-05-18 05:30:00
2001-05-18 06:00:00
2001-05-18 06:30:00
2001-05-18 07:00:00
2001-05-18 07:30:00
2001-05-18 08:00:00
2001-05-18 08:30:00
2001-05-18 09:00:00
2001-05-18 09:30:00
2001-05-18 10:00:00
2001-05-18 10:30:00
2001-05-18 11:00:00
2001-05-18 11:30:00
2001-05-18 12:00:00
2001-05-18 12:30:00
2001-05-18 13:00:00
2001-05-18 13:30:00
2001-05-18 14:00:00
2001-05-18 14:30:00
2001-05-18 15:00:00
2001-05-18 15:30:00
2001-05-18 16:00:00
2001-05-18 16:30:00
2001-05-18 17:00:00
2001-05-18 17:30:00
2001-05-18 18:00:00
2001-05-18 18:30:00
2001-05-18 19:00:00
2001-05-18 19:30:00
2001-05-18 20:00:00
2001-05-18 20:30:00
2001-05-18 21:00:00
2001-05-18 21:30:00


2001-05-26 10:00:00
2001-05-26 10:30:00
2001-05-26 11:00:00
2001-05-26 11:30:00
2001-05-26 12:00:00
2001-05-26 12:30:00
2001-05-26 13:00:00
2001-05-26 13:30:00
2001-05-26 14:00:00
2001-05-26 14:30:00
2001-05-26 15:00:00
2001-05-26 15:30:00
2001-05-26 16:00:00
2001-05-26 16:30:00
2001-05-26 17:00:00
2001-05-26 17:30:00
2001-05-26 18:00:00
2001-05-26 18:30:00
2001-05-26 19:00:00
2001-05-26 19:30:00
2001-05-26 20:00:00
2001-05-26 20:30:00
2001-05-26 21:00:00
2001-05-26 21:30:00
2001-05-26 22:00:00
2001-05-26 22:30:00
2001-05-26 23:00:00
2001-05-26 23:30:00
2001-05-27 00:00:00
2001-05-27 00:30:00
2001-05-27 01:00:00
2001-05-27 01:30:00
2001-05-27 02:00:00
2001-05-27 02:30:00
2001-05-27 03:00:00
2001-05-27 03:30:00
2001-05-27 04:00:00
2001-05-27 04:30:00
2001-05-27 05:00:00
2001-05-27 05:30:00
2001-05-27 06:00:00
2001-05-27 06:30:00
2001-05-27 07:00:00
2001-05-27 07:30:00
2001-05-27 08:00:00
2001-05-27 08:30:00
2001-05-27 09:00:00
2001-05-27 09:30:00
2001-05-27 10:00:00
2001-05-27 10:30:00


2001-06-03 23:30:00
2001-06-04 00:00:00
2001-06-04 00:30:00
2001-06-04 01:00:00
2001-06-04 01:30:00
2001-06-04 02:00:00
2001-06-04 02:30:00
2001-06-04 03:00:00
2001-06-04 03:30:00
2001-06-04 04:00:00
2001-06-04 04:30:00
2001-06-04 05:00:00
2001-06-04 05:30:00
2001-06-04 06:00:00
2001-06-04 06:30:00
2001-06-04 07:00:00
2001-06-04 07:30:00
2001-06-04 08:00:00
2001-06-04 08:30:00
2001-06-04 09:00:00
2001-06-04 09:30:00
2001-06-04 10:00:00
2001-06-04 10:30:00
2001-06-04 11:00:00
2001-06-04 11:30:00
2001-06-04 12:00:00
2001-06-04 12:30:00
2001-06-04 13:00:00
2001-06-04 13:30:00
2001-06-04 14:00:00
2001-06-04 14:30:00
2001-06-04 15:00:00
2001-06-04 15:30:00
2001-06-04 16:00:00
2001-06-04 16:30:00
2001-06-04 17:00:00
2001-06-04 17:30:00
2001-06-04 18:00:00
2001-06-04 18:30:00
2001-06-04 19:00:00
2001-06-04 19:30:00
2001-06-04 20:00:00
2001-06-04 20:30:00
2001-06-04 21:00:00
2001-06-04 21:30:00
2001-06-04 22:00:00
2001-06-04 22:30:00
2001-06-04 23:00:00
2001-06-04 23:30:00
2001-06-05 00:00:00


...

2019-08-21 04:00:00
2019-08-21 04:30:00
2019-08-21 05:00:00
2019-08-21 05:30:00
2019-08-21 06:00:00
2019-08-21 06:30:00
2019-08-21 07:00:00
2019-08-21 07:30:00
2019-08-21 08:00:00
2019-08-21 08:30:00
2019-08-21 09:00:00
2019-08-21 09:30:00
2019-08-21 10:00:00
2019-08-21 10:30:00
2019-08-21 11:00:00
2019-08-21 11:30:00
2019-08-21 12:00:00
2019-08-21 12:30:00
2019-08-21 13:00:00
2019-08-21 13:30:00
2019-08-21 14:00:00
2019-08-21 14:30:00
2019-08-21 15:00:00
2019-08-21 15:30:00
2019-08-21 16:00:00
2019-08-21 16:30:00
2019-08-21 17:00:00
2019-08-21 17:30:00
2019-08-21 18:00:00
2019-08-21 18:30:00
2019-08-21 19:00:00
2019-08-21 19:30:00
2019-08-21 20:00:00
2019-08-21 20:30:00
2019-08-21 21:00:00
2019-08-21 21:30:00
2019-08-21 22:00:00
2019-08-21 22:30:00
2019-08-21 23:00:00
2019-08-21 23:30:00
2019-08-22 00:00:00
2019-08-22 00:30:00
2019-08-22 01:00:00
2019-08-22 01:30:00
2019-08-22 02:00:00
2019-08-22 02:30:00
2019-08-22 03:00:00
2019-08-22 03:30:00
2019-08-22 04:00:00
2019-08-22 04:30:00


2019-08-29 17:00:00
2019-08-29 17:30:00
2019-08-29 18:00:00
2019-08-29 18:30:00
2019-08-29 19:00:00
2019-08-29 19:30:00
2019-08-29 20:00:00
2019-08-29 20:30:00
2019-08-29 21:00:00
2019-08-29 21:30:00
2019-08-29 22:00:00
2019-08-29 22:30:00
2019-08-29 23:00:00
2019-08-29 23:30:00
2019-08-30 00:00:00
2019-08-30 00:30:00
2019-08-30 01:00:00
2019-08-30 01:30:00
2019-08-30 02:00:00
2019-08-30 02:30:00
2019-08-30 03:00:00
2019-08-30 03:30:00
2019-08-30 04:00:00
2019-08-30 04:30:00
2019-08-30 05:00:00
2019-08-30 05:30:00
2019-08-30 06:00:00
2019-08-30 06:30:00
2019-08-30 07:00:00
2019-08-30 07:30:00
2019-08-30 08:00:00
2019-08-30 08:30:00
2019-08-30 09:00:00
2019-08-30 09:30:00
2019-08-30 10:00:00
2019-08-30 10:30:00
2019-08-30 11:00:00
2019-08-30 11:30:00
2019-08-30 12:00:00
2019-08-30 12:30:00
2019-08-30 13:00:00
2019-08-30 13:30:00
2019-08-30 14:00:00
2019-08-30 14:30:00
2019-08-30 15:00:00
2019-08-30 15:30:00
2019-08-30 16:00:00
2019-08-30 16:30:00
2019-08-30 17:00:00
2019-08-30 17:30:00


2019-09-07 06:00:00
2019-09-07 06:30:00
2019-09-07 07:00:00
2019-09-07 07:30:00
2019-09-07 08:00:00
2019-09-07 08:30:00
2019-09-07 09:00:00
2019-09-07 09:30:00
2019-09-07 10:00:00
2019-09-07 10:30:00
2019-09-07 11:00:00
2019-09-07 11:30:00
2019-09-07 12:00:00
2019-09-07 12:30:00
2019-09-07 13:00:00
2019-09-07 13:30:00
2019-09-07 14:00:00
2019-09-07 14:30:00
2019-09-07 15:00:00
2019-09-07 15:30:00
2019-09-07 16:00:00
2019-09-07 16:30:00
2019-09-07 17:00:00
2019-09-07 17:30:00
2019-09-07 18:00:00
2019-09-07 18:30:00
2019-09-07 19:00:00
2019-09-07 19:30:00
2019-09-07 20:00:00
2019-09-07 20:30:00
2019-09-07 21:00:00
2019-09-07 21:30:00
2019-09-07 22:00:00
2019-09-07 22:30:00
2019-09-07 23:00:00
2019-09-07 23:30:00
2019-09-08 00:00:00
2019-09-08 00:30:00
2019-09-08 01:00:00
2019-09-08 01:30:00
2019-09-08 02:00:00
2019-09-08 02:30:00
2019-09-08 03:00:00
2019-09-08 03:30:00
2019-09-08 04:00:00
2019-09-08 04:30:00
2019-09-08 05:00:00
2019-09-08 05:30:00
2019-09-08 06:00:00
2019-09-08 06:30:00


2019-09-15 19:30:00
2019-09-15 20:00:00
2019-09-15 20:30:00
2019-09-15 21:00:00
2019-09-15 21:30:00
2019-09-15 22:00:00
2019-09-15 22:30:00
2019-09-15 23:00:00
2019-09-15 23:30:00
2019-09-16 00:00:00
2019-09-16 00:30:00
2019-09-16 01:00:00
2019-09-16 01:30:00
2019-09-16 02:00:00
2019-09-16 02:30:00
2019-09-16 03:00:00
2019-09-16 03:30:00
2019-09-16 04:00:00
2019-09-16 04:30:00
2019-09-16 05:00:00
2019-09-16 05:30:00
2019-09-16 06:00:00
2019-09-16 06:30:00
2019-09-16 07:00:00
2019-09-16 07:30:00
2019-09-16 08:00:00
2019-09-16 08:30:00
2019-09-16 09:00:00
2019-09-16 09:30:00
2019-09-16 10:00:00
2019-09-16 10:30:00
2019-09-16 11:00:00
2019-09-16 11:30:00
2019-09-16 12:00:00
2019-09-16 12:30:00
2019-09-16 13:00:00
2019-09-16 13:30:00
2019-09-16 14:00:00
2019-09-16 14:30:00
2019-09-16 15:00:00
2019-09-16 15:30:00
2019-09-16 16:00:00
2019-09-16 16:30:00
2019-09-16 17:00:00
2019-09-16 17:30:00
2019-09-16 18:00:00
2019-09-16 18:30:00
2019-09-16 19:00:00
2019-09-16 19:30:00
2019-09-16 20:00:00


2019-09-24 09:00:00
2019-09-24 09:30:00
2019-09-24 10:00:00
2019-09-24 10:30:00
2019-09-24 11:00:00
2019-09-24 11:30:00
2019-09-24 12:00:00
2019-09-24 12:30:00
2019-09-24 13:00:00
2019-09-24 13:30:00
2019-09-24 14:00:00
2019-09-24 14:30:00
2019-09-24 15:00:00
2019-09-24 15:30:00
2019-09-24 16:00:00
2019-09-24 16:30:00
2019-09-24 17:00:00
2019-09-24 17:30:00
2019-09-24 18:00:00
2019-09-24 18:30:00
2019-09-24 19:00:00
2019-09-24 19:30:00
2019-09-24 20:00:00
2019-09-24 20:30:00
2019-09-24 21:00:00
2019-09-24 21:30:00
2019-09-24 22:00:00
2019-09-24 22:30:00
2019-09-24 23:00:00
2019-09-24 23:30:00
2019-09-25 00:00:00
2019-09-25 00:30:00
2019-09-25 01:00:00
2019-09-25 01:30:00
2019-09-25 02:00:00
2019-09-25 02:30:00
2019-09-25 03:00:00
2019-09-25 03:30:00
2019-09-25 04:00:00
2019-09-25 04:30:00
2019-09-25 05:00:00
2019-09-25 05:30:00
2019-09-25 06:00:00
2019-09-25 06:30:00
2019-09-25 07:00:00
2019-09-25 07:30:00
2019-09-25 08:00:00
2019-09-25 08:30:00
2019-09-25 09:00:00
2019-09-25 09:30:00


In [15]:
df.shape

(139081, 3)

In [16]:
#convert from mm/hr to total mm, mm/hr*0.5hr = mm 

df['mean_mm'] = df['mean_mmph']*0.5

df['max_mm'] = df['max_mmph']*0.5

#calculating total mm for morning, afternoon and evening based on gaoyun's definition 

df['hr_min'] = pd.to_datetime(df['LST']).dt.strftime('%H:%M')

df['date'] = pd.to_datetime(df['LST']).dt.date

def classify_time_of_day(time):
    
    if "06:00" <= time < "14:00": #8 hours x 2 = 16 total observations
        
        return 'morning'
    
    elif "14:00" <= time < "21:00": #7 hours x 2 = 14 total observations
        
        return 'afternoon'
    
    elif "21:00" <= time <= "23:30": #3 hours x 2 = 6 total observations
        
        return 'evening'

# # Apply the function to create a new column
df['time_of_day'] = df['hr_min'].apply(classify_time_of_day)

In [17]:
# List to store data for qualifying afternoon precipitation events
afternoon_precip_events_data = []

# Group data by 'date'
grouped = df.groupby('date')

# Process each group (date)
for date, group in grouped:

    # Find the hour with peak precipitation
    peak_hour = group.loc[group['mean_mm'].idxmax(), 'hr_min']
    
    peak_hour_is_afternoon = 14 <= int(peak_hour.split(':')[0]) <= 20
    
    # Sum precipitation by time of day
    morning_precip = group.loc[group['time_of_day'] == 'morning', 'mean_mm'].sum()
    afternoon_precip = group.loc[group['time_of_day'] == 'afternoon', 'mean_mm'].sum()
    evening_precip = group.loc[group['time_of_day'] == 'evening', 'mean_mm'].sum()

    # Check criteria
    if not peak_hour_is_afternoon:
        
        print(f"{date}: Disqualified because peak hour ({peak_hour}) is outside of 14:00-20:00.")
    
    elif afternoon_precip < 2 * morning_precip:
        
        print(f"{date}: Disqualified because afternoon precip ({afternoon_precip}) is less than 2x morning precip ({morning_precip}).")
    
    elif afternoon_precip <= evening_precip:
        
        print(f"{date}: Disqualified because afternoon precip ({afternoon_precip}) is not greater than evening precip ({evening_precip}).")
    
    else:
        # Add qualifying data to the list
        afternoon_precip_events_data.append(group)

# Combine all qualifying data into a single DataFrame
if afternoon_precip_events_data:
    
    qualifying_data = pd.concat(afternoon_precip_events_data, ignore_index=True)

else:
    
    qualifying_data = pd.DataFrame()  # Empty DataFrame if no events qualify

2001-05-01: Disqualified because peak hour (00:00) is outside of 14:00-20:00.
2001-05-02: Disqualified because peak hour (22:30) is outside of 14:00-20:00.
2001-05-03: Disqualified because peak hour (23:30) is outside of 14:00-20:00.
2001-05-04: Disqualified because afternoon precip (4.452927872538567) is less than 2x morning precip (4.585212484002113).
2001-05-05: Disqualified because peak hour (00:30) is outside of 14:00-20:00.
2001-05-07: Disqualified because peak hour (00:30) is outside of 14:00-20:00.
2001-05-12: Disqualified because peak hour (01:30) is outside of 14:00-20:00.
2001-05-15: Disqualified because peak hour (00:00) is outside of 14:00-20:00.
2001-05-16: Disqualified because peak hour (23:30) is outside of 14:00-20:00.
2001-05-17: Disqualified because peak hour (23:30) is outside of 14:00-20:00.
2001-05-18: Disqualified because peak hour (02:00) is outside of 14:00-20:00.
2001-05-19: Disqualified because afternoon precip (5.423966407775879) is less than 2x morning prec

2003-07-12: Disqualified because peak hour (03:30) is outside of 14:00-20:00.
2003-07-13: Disqualified because peak hour (10:30) is outside of 14:00-20:00.
2003-07-20: Disqualified because peak hour (21:00) is outside of 14:00-20:00.
2003-07-21: Disqualified because peak hour (23:30) is outside of 14:00-20:00.
2003-07-22: Disqualified because peak hour (00:00) is outside of 14:00-20:00.
2003-07-23: Disqualified because peak hour (06:00) is outside of 14:00-20:00.
2003-07-24: Disqualified because peak hour (00:00) is outside of 14:00-20:00.
2003-07-26: Disqualified because peak hour (23:30) is outside of 14:00-20:00.
2003-07-29: Disqualified because peak hour (22:30) is outside of 14:00-20:00.
2003-07-30: Disqualified because peak hour (01:30) is outside of 14:00-20:00.
2003-08-01: Disqualified because peak hour (23:30) is outside of 14:00-20:00.
2003-08-02: Disqualified because peak hour (05:00) is outside of 14:00-20:00.
2003-08-03: Disqualified because peak hour (05:30) is outside of

2005-08-30: Disqualified because peak hour (00:00) is outside of 14:00-20:00.
2005-08-31: Disqualified because afternoon precip (0.026341209158999845) is less than 2x morning precip (0.015780769150296692).
2005-09-01: Disqualified because peak hour (21:30) is outside of 14:00-20:00.
2005-09-02: Disqualified because peak hour (00:00) is outside of 14:00-20:00.
2005-09-07: Disqualified because peak hour (00:00) is outside of 14:00-20:00.
2005-09-08: Disqualified because afternoon precip (0.038229119847528636) is less than 2x morning precip (0.042183514044154435).
2005-09-12: Disqualified because peak hour (00:00) is outside of 14:00-20:00.
2005-09-13: Disqualified because afternoon precip (1.0085840350948274) is less than 2x morning precip (0.6620549485087395).
2005-09-14: Disqualified because peak hour (21:00) is outside of 14:00-20:00.
2005-09-15: Disqualified because peak hour (02:00) is outside of 14:00-20:00.
2005-09-16: Disqualified because peak hour (06:30) is outside of 14:00-20:

2009-08-07: Disqualified because peak hour (01:00) is outside of 14:00-20:00.
2009-08-08: Disqualified because peak hour (23:00) is outside of 14:00-20:00.
2009-08-11: Disqualified because peak hour (00:30) is outside of 14:00-20:00.
2009-08-13: Disqualified because peak hour (01:30) is outside of 14:00-20:00.
2009-08-15: Disqualified because peak hour (00:00) is outside of 14:00-20:00.
2009-08-16: Disqualified because peak hour (22:30) is outside of 14:00-20:00.
2009-08-17: Disqualified because peak hour (22:00) is outside of 14:00-20:00.
2009-08-18: Disqualified because peak hour (00:30) is outside of 14:00-20:00.
2009-08-19: Disqualified because peak hour (01:30) is outside of 14:00-20:00.
2009-08-20: Disqualified because peak hour (07:00) is outside of 14:00-20:00.
2009-08-21: Disqualified because peak hour (02:00) is outside of 14:00-20:00.
2009-08-26: Disqualified because peak hour (23:30) is outside of 14:00-20:00.
2009-08-27: Disqualified because peak hour (00:00) is outside of

2017-05-04: Disqualified because peak hour (03:00) is outside of 14:00-20:00.
2017-05-05: Disqualified because peak hour (01:30) is outside of 14:00-20:00.
2017-05-07: Disqualified because peak hour (22:30) is outside of 14:00-20:00.
2017-05-09: Disqualified because peak hour (21:30) is outside of 14:00-20:00.
2017-05-10: Disqualified because peak hour (21:00) is outside of 14:00-20:00.
2017-05-11: Disqualified because afternoon precip (2.0349708683788776) is less than 2x morning precip (1.0256148148328066).
2017-05-12: Disqualified because peak hour (02:00) is outside of 14:00-20:00.
2017-05-13: Disqualified because peak hour (03:00) is outside of 14:00-20:00.
2017-05-15: Disqualified because peak hour (23:00) is outside of 14:00-20:00.
2017-05-16: Disqualified because peak hour (22:30) is outside of 14:00-20:00.
2017-05-17: Disqualified because peak hour (02:00) is outside of 14:00-20:00.
2017-05-19: Disqualified because afternoon precip (3.5612844973802567) is less than 2x morning p

In [21]:
summary_ape_stats = qualifying_data.groupby('date')['max_mmph'].agg(['max']).reset_index()

# Rename columns for clarity
summary_ape_stats.columns = ['date', 'max_mmph_across_day']

In [32]:
c = sorted_max_mmph[sorted_max_mmph['max_mmph_across_day'] > 20]
c.shape

(447, 2)

In [35]:
with open("summary_ape_stats.pkl", "wb") as f:  # "wb" means write in binary mode
    
    pickle.dump(summary_ape_stats, f)

## investigating a single case

In [237]:
sgp_hh_means = []

for time in range(len(example_case)): 

    test_array = example_case[time][1].data

    sgp_hh_means.append((example_case[time][0], np.mean(test_array)))

    time_for_title = example_case[time][0]

    lons = lon_lat_indices[0][0]

    lats = lon_lat_indices[0][1]

    lon_grid, lat_grid = np.meshgrid(lons, lats)

    fig, ax = plt.subplots(figsize=(9, 5), subplot_kw={'projection': ccrs.PlateCarree()})

    precip_plot = ax.pcolormesh(lon_grid, lat_grid, test_array.T, cmap='Blues', transform=ccrs.PlateCarree())

    # Add features to the map
    ax.add_feature(cfeature.COASTLINE, linewidth=0.5)

    ax.add_feature(cfeature.BORDERS, linewidth=0.5)

    ax.add_feature(cfeature.STATES, linewidth=0.5, edgecolor='gray')

    ax.gridlines(draw_labels=True, linestyle="--", color="gray", alpha=0.5)

    # Add colorbar
    cbar = plt.colorbar(precip_plot, ax=ax, orientation='vertical', shrink=0.7, pad=0.1)

    cbar.set_label('Precipitation (mm)')

    # Set map extent (optional)
    ax.set_extent([lon_grid.min(), lon_grid.max(), lat_grid.min(), lat_grid.max()], crs=ccrs.PlateCarree())

    # Add title
    ax.set_title("Precipitation Map {}".format(time_for_title), fontsize=14)

    # Show the plot
    plt.show()


In [187]:
sgp_hh_means_df = pd.DataFrame(sgp_hh_means, columns=['time', 'p'])

morning = np.sum(sgp_hh_means_df['p'][12:28])

aft = np.sum(sgp_hh_means_df['p'][28:42])

night = np.sum(sgp_hh_means_df['p'][42:])

sorted_hh = sgp_hh_means_df.sort_values(by='p', ascending=False).reset_index(drop=True)

max_hour = sorted_hh['time'][0].hour

print("condition 1 satisfied: ", (aft > night) & (aft >= 2*morning))
print("condition 2 satisfied", max_hour in (14, 15, 16, 17, 18, 19, 20))
print("max hour is: ", max_hour)

condition 1 satisfied:  False
condition 2 satisfied True
max hour is:  16
